In [53]:
import pandas as pd
import pickle

#Working directory tools
from pathlib import Path
import os
from os import listdir
cwd = 'F:\Santiago\Arfima\Projects\Dashboard_lite'

import sys
module_path = os.path.abspath(os.path.join('.'))
if module_path not in sys.path:
    sys.path.append(module_path)

import numpy as np
import pandas as pd

#Plotly graphs
import plotly.graph_objs as go
import dash
import dash_html_components as html
import dash_core_components as dcc
import ipywidgets as ipw

from datetime import datetime, timedelta

#Max display (monitor)
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>")) #70%

#Sklearn
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import PolynomialFeatures

os.chdir(cwd)
os.getcwd()

'F:\\Santiago\\Arfima\\Projects\\Dashboard_lite'

In [54]:
import config as cf
from Scripts import functions as f
from Scripts import ffs_functions as ff
from Scripts import launch

#App plot layout styles
from styles import (style_curve, style_hist, style_line, style_table, style_scatter)

launch.update_globals('FedFunds')

##DATA
FFsDataDfDict = ff.loadData()

In [55]:
HTML(
'''<script>
  function code_toggle() {
    if (code_shown){
      $('div.input').hide('500');
      $('#toggleButton').val('Show Code')
    } else {
      $('div.input').show('500');
      $('#toggleButton').val('Hide Code')
    }
    code_shown = !code_shown
  }

  $( document ).ready(function(){
    code_shown=false;
    $('div.input').hide()
  });
</script>
<form action="javascript:code_toggle()"><input type="submit" id="toggleButton" value="Show Code"></form>''')

### Parameters & Templates

In [56]:
#TABLE GENERIC TEMPLATE
############################################################
headers = [
    'Trace', 'count', 
    'mean', 'std', 
    'min', 
    '1%', '5%', 
    '25%', '50%', 
    '75%', '95%', 
    '99%',
    'max']

#Header dict
Header = {
  'values': [
    '<b>' + headers[i] + '</b>'  
    for i in range(0, len(headers))
  ],
  'align': 'center',
  'fill_color': '#393C43',
  'line_color': '#393C43',    
  'height': 30, 
  'font': {
    'size': 13, 'family': 'Roboto', 
    'color': '#F9FAF2'
  }
}

#Cells dict
Cells = {
  'values': None,
  'align': 'center',
  'format': [[''], ['.0f']] + 
    [['.2f'] for i in range(0, len(headers) - 2)],
  'fill_color': cf.plotStyle['general']['paper_bgcolor'],
  'line_color': cf.plotStyle['general']['paper_bgcolor'],    
  'height': 25, 
  'font': {
    'size': [12]  + 
      [13 for i in range(0, len(headers) - 1)], 
    'family': 'Roboto', 
    'color': ['#F9FAF2']  + 
      ['#0BB3F1' for i in range(0, len(headers) - 1)]
  }
}    

#Table object
SummaryTablePlot = go.Table(header = Header, cells = Cells)
############################################################

def dashTableWrapper_1(data_Df, title, TableTemplate, tableHeight):
    
    #Table figure
    wrapperTable = go.Figure(
        TableTemplate, go.Layout(**style_table.dark)
    )
    
    #Table title
    wrapperTable.layout.title.text = title
    
    #Table layout 
    wrapperTable.layout.paper_bgcolor = '#2F3136'
    wrapperTable.layout.plot_bgcolor = '#2F3136' 
    wrapperTable.layout.height = tableHeight
    wrapperTable.layout.title.y = 0.98
    
    #Insert data
    wrapperTable.data[0].cells.values = [
      data_Df.iloc[:, i] for 
      i in range(0, len(data_Df.T))
    ]
    
    return wrapperTable

In [57]:
#CROSS SECTION PLOT TEMPLATE
############################################################
def dashPlotWrapper_1(plotData, title, xaxisLabel, yaxisLabel):
    
    #Median plot
    MedianPlot = [go.Scatter(
      x = plotData.columns, 
      y = plotData.iloc[i, :], 
      mode ='lines+markers', 
      name = plotData.iloc[i, :].name.strftime('%Y-%m-%d'),
      visible = True,
      showlegend = False,
      opacity = 0.9,                           
      line_width = 3,
      marker_size = 6,     
      marker_symbol = 'circle') for i in range(0, len(plotData))
    ]    
    
    #Figure
    wrapperfig = go.Figure(
        MedianPlot, go.Layout(**style_curve.dark)
    )    
    
    #Figure title
    wrapperfig.layout.title.text = title   
    
    #Additional fig layout params
    wrapperfig.layout.height = 600 
    wrapperfig.layout.width = 1000 

    wrapperfig.layout.paper_bgcolor = '#2F3136'
    wrapperfig.layout.plot_bgcolor = '#2F3136'
    wrapperfig.layout.hovermode = 'closest'

    wrapperfig.layout.xaxis.title.text = xaxisLabel
    wrapperfig.layout.yaxis.title.text = yaxisLabel 
    
    return wrapperfig

In [58]:
#CROSS SECTION DISTRIBUTION PLOT TEMPLATE
############################################################
def dashPlotWrapper_2(
    StatsDf, title, xaxisLabel, yaxisLabel, 
    TimeSeriesDf = [], ids_strategy = [], Colors = [],
    StatIndices = [['5%', '95%'], ['10%', '90%'], ['25%', '75%']],
    width = 1000, height = 600, smoothing = 0, 
    median_line_width = 4, returnFig = True
):
    
    #Distribution plot parameters:
    ColorStats = ['#0BB3F1', '#08E6FF', '#266185']
    filltype = [None, 'tonexty']
    ShowL = [False, True]  
    
    
    #Plot(s) object(s):
    
    #Plot1: Distribution plots (quantiles)
    ##############################################
    DistrTsPlot = []
    for j in range(0, len(StatIndices)):

        plotData = StatsDf.loc[StatIndices[j], :]

        SubPlot = [go.Scatter(
            x = plotData.columns, 
            y = plotData.iloc[i, :], 
            name = plotData.index[i],
            showlegend = ShowL[i],
            mode =  'lines', 
            visible = True,                          
            line_color = ColorStats[j],
            line_width = 0, 
            line_shape = 'spline',
            line_smoothing = smoothing, 
            fill = filltype[i], 
            hoveron = 'points') for i in range(0, 2)
        ]

        DistrTsPlot += SubPlot
    ##############################################  

        
    #Plot2:Extreme values plot (min/max)
    ##############################################
    plotData = StatsDf.loc[['min', 'max'], :]

    ExtrTsPlot = [go.Scatter(
        x = plotData.columns, 
        y = plotData.iloc[i, :], 
        name = plotData.index[i],                    
        mode =  'markers', 
        visible = 'legendonly',
        opacity = 1,                           
        marker_color = '#F14B6B',
        marker_size = 4,
        marker_symbol = 'diamond',
        hoveron = 'points') for i in range(0, 2)
    ]
    ##############################################

    #Plot3:Median curve plot  
    ##############################################
    plotData = StatsDf.loc['50%', :]

    MedianPlot = [go.Scatter(
        x = plotData.index, 
        y = plotData, 
        name = 'Median', 
        mode ='lines', 
        visible = True,
        opacity = 0.9,                           
        line_color = 'white',
        line_width = median_line_width,
        line_shape = 'spline',
        line_smoothing = smoothing)
    ]
    ##############################################

    #Plot4:Time series  
    ##############################################
    plotData = TimeSeriesDf

    MainTsPlot = [go.Scatter(
        x = plotDf.index, 
        y = plotDf[ids_strategy[i]], 
        name = ids_strategy[i], 
        mode ='lines', 
        visible = True, 
        opacity = 0.9, 
        line_color = Colors[i],
        line_width = 3) for i in range(0, len(ids_strategy))
    ] 
    ##############################################    
    
    #Figure
    wrapperfig = go.Figure(
        (DistrTsPlot + ExtrTsPlot + MedianPlot + MainTsPlot), 
        go.Layout(**style_curve.dark)
    )      
    
    #Figure title
    wrapperfig.layout.title.text = title   
    
    #Additional fig layout params
    wrapperfig.layout.height = height 
    wrapperfig.layout.width = width 

    wrapperfig.layout.paper_bgcolor = '#2F3136'
    wrapperfig.layout.plot_bgcolor = '#2F3136'

    wrapperfig.layout.xaxis.title.text = xaxisLabel
    wrapperfig.layout.yaxis.title.text = yaxisLabel 

    return (
        wrapperfig if returnFig 
        else (DistrTsPlot, ExtrTsPlot, MedianPlot, MainTsPlot)
    )

In [59]:
#TIME SERIES PLOT TEMPLATE
############################################################
def dashPlotWrapper_3(plotDf, ids_strategy, title, 
                      xaxisLabel, yaxisLabel, Colors,
                      width = 1000, height = 600,
                      returnFig = True,
                     ):
  
    
    #Plot object
    MainTsPlot = [go.Scatter(
        x = plotDf.index, 
        y = plotDf[ids_strategy[i]], 
        name = ids_strategy[i], 
        mode ='lines', 
        visible = True, 
        opacity = 0.9, 
        line_color = Colors[i],
        line_width = 2) for i in range(0, len(ids_strategy))
    ]   

    #Figure
    wrapperfig = go.Figure(
        MainTsPlot, go.Layout(**style_line.dark)
    ) 

    #Figure title
    wrapperfig.layout.title.text = title

    wrapperfig.layout.title.y = 0.92 

    #Additional fig layout params
    wrapperfig.layout.height = height 
    wrapperfig.layout.width = width 

    wrapperfig.layout.paper_bgcolor = '#2F3136'
    wrapperfig.layout.plot_bgcolor = '#2F3136'

    wrapperfig.layout.xaxis.title.text = xaxisLabel
    wrapperfig.layout.yaxis.title.text = yaxisLabel  
    
    return wrapperfig if returnFig else MainTsPlot 

In [60]:
#BAR TIME SERIES PLOT TEMPLATE
############################################################
def dashPlotWrapper_4(plotDf, ids_strategy, title, 
                      xaxisLabel, yaxisLabel, Colors,
                      width = 1000, height = 600,
                      zeroline = True, zerolinecolor = 'white',
                      zerolinewidth = 2,
                      returnFig = True,
                     ):
  
    
    #Plot object
    MainBarPlot = [go.Bar(
        x = plotDf.index, 
        y = plotDf[ids_strategy[i]], 
        name = ids_strategy[i], 
        visible = True, 
        opacity = 0.9, 
        marker_color = Colors[i],
        marker_line_color = '#1ABD9C',
        marker_line_width = 0) for i in range(0, len(ids_strategy))
    ]   

    #Figure
    wrapperfig = go.Figure(
        MainBarPlot, go.Layout(**style_line.dark)
    ) 

    #Figure title
    wrapperfig.layout.title.text = title

    wrapperfig.layout.title.y = 0.92 

    #Additional fig layout params
    wrapperfig.layout.height = height 
    wrapperfig.layout.width = width 

    wrapperfig.layout.paper_bgcolor = '#2F3136'
    wrapperfig.layout.plot_bgcolor = '#2F3136'

    wrapperfig.layout.xaxis.title.text = xaxisLabel
    wrapperfig.layout.yaxis.title.text = yaxisLabel 
    
    wrapperfig.layout.yaxis.zeroline = zeroline
    wrapperfig.layout.yaxis.zerolinecolor = zerolinecolor
    wrapperfig.layout.yaxis.zerolinewidth = zerolinewidth
    
    return wrapperfig if returnFig else MainBarPlot 

In [61]:
#HISTOGRAM PLOT TEMPLATE
############################################################
def dashPlotWrapper_5(plotDf, ids_strategy, title, 
                      xaxisLabel, yaxisLabel, Colors,
                      width = 1000, height = 600,  
                      opacity = 0.8, returnFig = True,
                     ):
    
    #Plot object
    MainHistPlot = [go.Histogram(
        y = plotDf[ids_strategy[i]], 
        name = ids_strategy[i], 
        opacity = opacity,
        marker_color = Colors[i],
        marker_line_width = 1,
        marker_line_color = '#303136',  
        visible = True) for i in range(0, len(ids_strategy))
    ] 

    #Figure
    wrapperfig =  go.Figure(
        MainHistPlot, go.Layout(**style_hist.dark_v)
    )

    #Figure title
    wrapperfig.layout.title.text = title

    wrapperfig.layout.title.y = 0.92 

    #Additional fig layout params
    wrapperfig.layout.height = height 
    wrapperfig.layout.width = width 

    wrapperfig.layout.paper_bgcolor = '#2F3136'
    wrapperfig.layout.plot_bgcolor = '#2F3136'

    wrapperfig.layout.xaxis.title.text = xaxisLabel
    wrapperfig.layout.yaxis.title.text = yaxisLabel 
    
    return wrapperfig if returnFig else MainHistPlot   

In [62]:
#HISTOGRAM PLOT TEMPLATE
############################################################
def dashPlotWrapper_6(plotDf, ids_strategy, title, 
                      xaxisLabel, yaxisLabel, Colors,
                      width = 1000, height = 600, 
                      opacity = 0.8, returnFig = True,
                     ):
    
    #Plot object
    MainHistPlot = [go.Histogram(
        x = plotDf[ids_strategy[i]], 
        name = ids_strategy[i], 
        opacity = opacity,
        marker_color = Colors[i],
        marker_line_width = 1,
        marker_line_color = '#303136',  
        visible = True) for i in range(0, len(ids_strategy))
    ] 

    #Figure
    wrapperfig =  go.Figure(
        MainHistPlot, go.Layout(**style_hist.dark_h)
    )

    #Figure title
    wrapperfig.layout.title.text = title

    wrapperfig.layout.title.y = 0.92 

    #Additional fig layout params
    wrapperfig.layout.height = height 
    wrapperfig.layout.width = width 

    wrapperfig.layout.paper_bgcolor = '#2F3136'
    wrapperfig.layout.plot_bgcolor = '#2F3136'

    wrapperfig.layout.xaxis.title.text = xaxisLabel
    wrapperfig.layout.yaxis.title.text = yaxisLabel 
    
    return wrapperfig if returnFig else MainHistPlot   

In [63]:
#GET STRAT DATA WRAPPER
############################################################
def GetStratData(
    strategies_options, strategyClass, 
    strategy, length, multiplier, option_yield, 
    startDate, endDate, keyDate = None, 
    daysBefore = 0, daysAfter = 0
):
    
    #Update main_df & number of generic contracts
    cf.main_df = cf.main_dfs[strategyClass]
    cf.number_contracts = cf.number_generics[strategyClass]
    
    #Check if computing the strategy is viable for each contract
    #based on the selected strategy class, then filter strategies
    strategy = [c for c in strategy if 
      ff.proceed_with_strategy(
          strategies_options, strategyClass, length, 
          c, cf.number_contracts, cf.main_df
      )]

    #Iterate on every selected ticker and calculate the strategy,
    #strategy id's and add them to the main dataframe
    ids_strategy = list()
    dates_strategy = pd.DataFrame(
      index = ['Start', 'Expiration', 
        'FirstDayAvailable', 'LastDayAvailable'], 
      columns = strategy,
    )    
    for c in strategy:
        
        #Get strategy labels
        labels = ff.calculate_strategy_labels(
            strategies_options, strategyClass, length, 
            c, cf.number_contracts, cf.main_df
        )          

        #Compute relevant dates (start, expiry, first and last available)    
        dates_strategy.loc[:, c] = ff.GetTickerD_full(
            labels, strategyClass, cf.number_contracts, 
            cf.main_df, cf.ticker_dfs
        )        
        
        #Compute the strategy        
        calculated_strategy = ff.calculate_strategy(
            labels, strategies_options, strategyClass, length, c, 
            cf.number_contracts, cf.main_df, cf.ticker_dfs,
            cf.weights_df
        ) 

        #Strategy id        
        id_strategy = ff.get_strategy_id(strategies_options, 
        strategyClass, length, c, cf.number_contracts, cf.main_df) 

        #Save in memory
        f.save_strategy(id_strategy, calculated_strategy) 

        ids_strategy.append(id_strategy) 

    #Plot data frame (filter by strategies & dates)
    plotDf = cf.main_df[ids_strategy][startDate:endDate] * float(multiplier)
    
    #Key date data frame transformation (net change before/after key date)
    if keyDate is not None:
        
        #Copy data
        plotNcDf = plotDf.copy()        
    
        #Compute cumulative net changes before and after the key date
        plotNcDf[:keyDate] = plotDf[:keyDate].loc[::-1].diff().cumsum().loc[::-1]
        plotNcDf[keyDate:] = plotDf[keyDate:].diff().cumsum()

        #Create the plotting indices +- days before and after the key date
        plotNcDf['NcCount'] = (
          [str(i) for i in range(-len(plotDf[:keyDate]) + 1, 1)] + 
          [str(i) for i in range(1, len(plotDf[keyDate:]))]
        )

        #Key date to timestamp for indexing 
        keyDateTs = pd.Timestamp(keyDate)

        #Get key date location on the plot data frame
        keyDateLoc = plotNcDf.index.get_loc(keyDateTs)

        #Fix number of days before/after the key date if they exceed limits
        beforeIndex = (
          0 if daysBefore > keyDateLoc else 
          (keyDateLoc - daysBefore)
        )

        afterIndex = (
          len(plotNcDf) if (keyDateLoc + 1 + daysAfter) > len(plotNcDf) else 
          (keyDateLoc + 1 + daysAfter)
        )

        #Plot data frame, filtered by keydate and keydate span
        plotDf = plotNcDf.iloc[range(beforeIndex, afterIndex)]

        #Get key date location on the trimmed plot data frame  
        keyDateLoc_2 = plotDf.index.get_loc(keyDateTs)         

        #Key date values changed to 0  
        plotDf.iloc[keyDateLoc_2, :] = (
          plotDf.iloc[keyDateLoc_2, :].replace(np.nan, 0)
        )    
    
    return plotDf, ids_strategy    

In [64]:
heatmap_syle_dark = {
  'title': {
    'x': 0.5, 
    'y': 0.92,  
    'font': {
      'size': 14, 
      'family': 'Roboto', 
      'color': '#9E9EAA',
    },
  }, 
  'margin': {
    't': 60, 
    'b': 50, 
    'l': 60, 
    'r': 10,
  },
  'hoverlabel': {
    'bgcolor': '#111', 
    'bordercolor': '#363940', 
    'font_color': '#D5D8DD',
    'font_family': 'Roboto',
  }, 
  'xaxis': {
    'title': {
      'font': {
        'size': 13,
        'family': 'Roboto', 
        'color': '#9E9EAA',
      },
      'standoff': 0,
    },
    'ticks': 'outside',
    'ticklen': 8,
    'tickcolor': '#303136',    
    'color': '#9E9EAA', 
    'showline': True, 
    'linecolor': 'rgba(83, 83, 95 ,.3)', 
    'showspikes': False,
    'showgrid': False,
    'gridcolor': '#303136', 
    'zeroline': False,
    'spikethickness': 2, 
    'spikecolor': '#DE2369',
  }, 
  'yaxis': {
    'title': {
      'font': {
        'size': 13, 
        'family': 'Roboto', 
        'color': '#9E9EAA',
      }, 
      'standoff': 0,
    },
    'ticks': 'outside',
    'ticklen': 8,
    'tickcolor': '#303136',    
    'color': '#9E9EAA',
    'showgrid': False,
    'zeroline': False,                                  
    'side': 'left', 
    'showspikes': False,
    'spikethickness': 2, 
    'spikecolor': '#DE2369',
  }, 
  'legend': {
    'font': {
      'size': 13, 
      'family': 'Roboto',
      'color': '#9E9EAA',
    },
    'bgcolor': cf.plotStyle['general']['legend_bgcolor'],
    'orientation':'h',
    'x': 1,
    'y': 1.08,
    'xanchor': 'auto',
  },
  'transition': {
    'duration': 0, #200
  }, 
  'modebar': {
    'bgcolor': cf.plotStyle['general']['modebar_bgcolor'],
  },  
  'autosize': True,
  'paper_bgcolor': cf.plotStyle['general']['paper_bgcolor'],
  'plot_bgcolor': cf.plotStyle['general']['plot_bgcolor'],   
}

heatmap_syle_cbar_dark = {
  'title': {
    'font': {
      'size': 14, 
      'family': 'Roboto', 
      'color': '#9E9EAA',
    },
  }, 
  'tickfont' : {
    'size': 13, 
    'family': 'Roboto', 
    'color': '#9E9EAA',      
  }, 
}

In [65]:
def KellyCQxsize(payoff, p, q, totalSize):
    
    f = (payoff * p - q) / payoff
    
    return f

## PLOTS

#### Params

In [66]:
params_dict = {
    
    'Hikes_grpHikes': {
        'strategyClass' : 'Hike',
        'option_yield' : 'price',
        'length' : 1,
        'multiplier' : 1,
        'strategies' : ['Z22', 'G23', 'H23', 'K23'],        
    },   
    
    'Hikes_grpCuts':{
        'strategyClass' : 'Hike',
        'option_yield' : 'price',
        'length' : 1,
        'multiplier' : 1,
        'strategies' : ['M23', 'N23', 'U23', 'X23', 'Z23', 'F24', 'H24', 'K24'],  
    },
    
}

Colors =[
    '#0BB3F1', '#F14B6B', 
    '#00FFAE', '#0BDBF1',
    '#F21D6B', 
    '#A0CDE2', '#D5D8DD', 
    '#1ABD9C', '#3CDBCC', 'yellow',
]

Data_Df_dict = {}

#### Hikes Group 1: Hikes (front)

In [67]:
Strats = 'Hikes_grpHikes'
#startDate = '2022-07-01'
startDate = '2022-09-21'
endDate = cf.main_dfs['Hike'].index[-1].strftime('%Y-%m-%d')
#keyDate = '07-01-2022'
keyDate = '2022-09-21'
daysBefore = 0 
daysAfter = 90

plotDf, ids_strategy = GetStratData(
    cf.strategies_options, 
    params_dict[Strats]['strategyClass'], 
    params_dict[Strats]['strategies'], 
    params_dict[Strats]['length'], 
    params_dict[Strats]['multiplier'], 
    params_dict[Strats]['option_yield'], 
    startDate, endDate, keyDate,
    daysBefore, daysAfter
)

#Data frames
plotDf = plotDf.iloc[:, :-1]
plotDf_Nc = plotDf.diff()

#STATS
Stats_Df = plotDf.T.describe(percentiles = [.01, .05, .10, .25, .5, .75, .90, .95, .99]).T
Stats_Nc_Df = plotDf_Nc.describe(percentiles = [.01, .05, .10, .25, .5, .75, .90, .95, .99]).T
plotDf_Zscores = (plotDf.T - Stats_Df['50%']).T

#Store
Data_Df_dict[Strats] = plotDf

In [68]:
dashPlotWrapper_4(
    plotDf_Nc.dropna(), ids_strategy, 
    Strats + ' - ' + 'Net change' + ' from ' + startDate + ' to ' + endDate, 
    'Date', 'Net change', 
    Colors, height = 632, width = 1532,
    zerolinewidth = 1,
    returnFig = True,
)

In [69]:
dashPlotWrapper_2(
    Stats_Df.T, 
    Strats + ' - ' + 'Cumulative net change' + ' from ' + startDate + ' to ' + endDate, 
    'Date', 'Cumulative Net Change',
    plotDf, ids_strategy, Colors,
    StatIndices = [['10%', '90%'], ['25%', '75%']],
    height = 632, width = 1532, smoothing = 0.2,
)

In [70]:
dashPlotWrapper_4(
    plotDf_Zscores.dropna(), ids_strategy, 
    Strats + ' - ' + 'Zscore to median' + ' from ' + startDate + ' to ' + endDate, 
    'Date', 'Zscore', 
    Colors, height = 632, width = 1532,
    zerolinewidth = 1,
    returnFig = True,
)

In [71]:
figlist = []
for strategy in ids_strategy:
    
    fig1 = dashPlotWrapper_2(
        Stats_Df.T, strategy, 
        'Date', 'Cumulative Net Change',
        plotDf[strategy], [strategy], Colors[1:],
        StatIndices = [['10%', '90%'], ['25%', '75%']],
        width = 712, height = 392, smoothing = 0.2,
        median_line_width = 3
    )
    
    fig2 = dashPlotWrapper_6(
        plotDf_Nc, [strategy], 
        'Net Change', None, None,
        Colors[1:], width = 312, height = 392, 
        opacity = 1,
    ) 
    
    fig3 = dashPlotWrapper_6(
        plotDf_Zscores, [strategy], 
        'Zscore Distr', None, None,
        Colors[1:], width = 312, height = 392, 
        opacity = 1,
    ) 
    
    fig4 = dashPlotWrapper_4(
        plotDf_Zscores, [strategy], 
        'Zscore Ts', None, None, 
        Colors, width = 472, height = 392
    )    
    
    figlist += [go.FigureWidget(fig1), 
                go.FigureWidget(fig2), 
                go.FigureWidget(fig3),
                go.FigureWidget(fig4)]
    
ipw.GridBox(figlist, 
            layout = {
                'grid_template_columns':'712px 312px 312px 472px', 
                'grid_template_rows':'auto',
                
            }
           )     

GridBox(children=(FigureWidget({
    'data': [{'hoveron': 'points',
              'line': {'color': '#0BB3F1',…

#### Hikes Group 2: Cuts (back)

In [72]:
Strats = 'Hikes_grpCuts'
#startDate = '2022-07-01'
startDate = '2022-09-21'
endDate = cf.main_dfs['Hike'].index[-1].strftime('%Y-%m-%d')
#keyDate = '07-01-2022'
keyDate = '2022-09-21'
daysBefore = 0 
daysAfter = 90

plotDf, ids_strategy = GetStratData(
    cf.strategies_options, 
    params_dict[Strats]['strategyClass'], 
    params_dict[Strats]['strategies'], 
    params_dict[Strats]['length'], 
    params_dict[Strats]['multiplier'], 
    params_dict[Strats]['option_yield'], 
    startDate, endDate, keyDate,
    daysBefore, daysAfter
)

#Data frames
plotDf = plotDf.iloc[:, :-1]
plotDf_Nc = plotDf.diff()

#STATS
Stats_Df = plotDf.T.describe(percentiles = [.01, .05, .10, .25, .5, .75, .90, .95, .99]).T
Stats_Nc_Df = plotDf_Nc.describe(percentiles = [.01, .05, .10, .25, .5, .75, .90, .95, .99]).T
plotDf_Zscores = (plotDf.T - Stats_Df['50%']).T

#Store
Data_Df_dict[Strats] = plotDf

In [73]:
dashPlotWrapper_4(
    plotDf_Nc.dropna(), ids_strategy, 
    Strats + ' - ' + 'Net change' + ' from ' + startDate + ' to ' + endDate, 
    'Date', 'Net change', 
    Colors, height = 632, width = 1532,
    zerolinewidth = 1,
    returnFig = True,
)

In [74]:
dashPlotWrapper_2(
    Stats_Df.T, 
    Strats + ' - ' + 'Cumulative net change' + ' from ' + startDate + ' to ' + endDate, 
    'Date', 'Cumulative Net Change',
    plotDf, ids_strategy, Colors,
    StatIndices = [['10%', '90%'], ['25%', '75%']],
    height = 632, width = 1532, smoothing = 0.2,
)

In [75]:
dashPlotWrapper_4(
    plotDf_Zscores.dropna(), ids_strategy, 
    Strats + ' - ' + 'Zscore to median' + ' from ' + startDate + ' to ' + endDate, 
    'Date', 'Zscore', 
    Colors, height = 632, width = 1532,
    zerolinewidth = 1,
    returnFig = True,
)

In [76]:
figlist = []
for strategy in ids_strategy:
    
    fig1 = dashPlotWrapper_2(
        Stats_Df.T, strategy, 
        'Date', 'Cumulative Net Change',
        plotDf[strategy], [strategy], Colors[1:],
        StatIndices = [['10%', '90%'], ['25%', '75%']],
        width = 712, height = 392, smoothing = 0.2,
        median_line_width = 3
    )
    
    fig2 = dashPlotWrapper_6(
        plotDf_Nc, [strategy], 
        'Net Change', None, None,
        Colors[1:], width = 312, height = 392, 
        opacity = 1,
    ) 
    
    fig3 = dashPlotWrapper_6(
        plotDf_Zscores, [strategy], 
        'Zscore Distr', None, None,
        Colors[1:], width = 312, height = 392, 
        opacity = 1,
    ) 
    
    fig4 = dashPlotWrapper_4(
        plotDf_Zscores, [strategy], 
        'Zscore Ts', None, None, 
        Colors, width = 472, height = 392
    )    
    
    figlist += [go.FigureWidget(fig1), 
                go.FigureWidget(fig2), 
                go.FigureWidget(fig3),
                go.FigureWidget(fig4)]
    
ipw.GridBox(figlist, 
            layout = {
                'grid_template_columns':'712px 312px 312px 472px', 
                'grid_template_rows':'auto',
                
            }
           )     

GridBox(children=(FigureWidget({
    'data': [{'hoveron': 'points',
              'line': {'color': '#0BB3F1',…

#### CORRELATIONS

In [77]:
HeatMap_df = pd.concat(Data_Df_dict.values(), axis = 1, ignore_index=False, sort = False).corr()
#HeatMap_df = np.triu(np.ones(CorrDf.shape)) * HeatMap_df

#Plot object
CorrHeatPlot = [go.Heatmap(
z = HeatMap_df,
x = HeatMap_df.columns.tolist(),
y = HeatMap_df.index.tolist(),
name = 'Correlations',
hoverongaps = False,
opacity = 0.9,
colorscale = ['#F14B6B', '#F1736B', 'white', '#3DE7F5', '#0BB3F1'],
colorbar = heatmap_syle_cbar_dark)]

#Figure
wrapperfig =  go.Figure(
    CorrHeatPlot, go.Layout(**heatmap_syle_dark)
)

#Figure title
wrapperfig.layout.title.text = (
    'Both Hike groups correlations - ' + 
    startDate + ' to ' + endDate

)

wrapperfig.layout.title.y = 0.94 

#Additional fig layout params
wrapperfig.layout.height = 642
wrapperfig.layout.width = 972 

wrapperfig.layout.paper_bgcolor = '#2F3136'
wrapperfig.layout.plot_bgcolor = '#2F3136'

wrapperfig